#Installing libraries


In [29]:
!pip install Plotly==4.12

!pip install dash
!pip install dash-html-components
!pip install dash-core-components
!pip install dash-table

In [30]:
import os.path
import sys, json
import requests
import subprocess

import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

from requests.exceptions import RequestException
from requests.adapters import HTTPAdapter
from requests.packages.urllib3.util.retry import Retry


from collections import namedtuple

#Configuring the Ngrok


In [31]:
def download_ngrok():
    if not os.path.isfile('ngrok'):
        !wget https://bin.equinox.io/c/4VmDzA7iaHb/ngrok-stable-linux-amd64.zip
        !unzip -o ngrok-stable-linux-amd64.zip
    pass

In [32]:
Response = namedtuple('Response', ['url', 'error'])

def get_tunnel():
    try:
        Tunnel = subprocess.Popen(['./ngrok','http','8050'])

        session = requests.Session()
        retry = Retry(connect=3, backoff_factor=0.5)
        adapter = HTTPAdapter(max_retries=retry)
        session.mount('http://', adapter)

        res = session.get('http://localhost:4040/api/tunnels')
        res.raise_for_status()

        tunnel_str = res.text
        tunnel_cfg = json.loads(tunnel_str)
        tunnel_url = tunnel_cfg['tunnels'][0]['public_url']

        return Response(url=tunnel_url, error=None)
    except RequestException as e:
        return Response(url=None, error=str(e))

# Reading data

In [33]:
data = pd.read_csv('/content/archive.zip', compression='zip', encoding='ISO-8859-1')

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning:

Columns (4,6,31,33,61,62,63,76,79,90,92,94,96,114,115,121) have mixed types.Specify dtype option on import or set low_memory=False.



In [34]:
df = data[['eventid', 'iyear', 'imonth', 'iday', 'country', 'country_txt', 'region',
          'region_txt', 'city', 'latitude', 'longitude', 'multiple', 'success', 
          'attacktype1_txt', 'targtype1_txt', 'nkill']].copy()

#Renaming attack type column
df.rename(columns = {"attacktype1_txt": "attacktype"}, inplace=True)

df.head()          

eventid  iyear  ...                targtype1_txt  nkill
0  197000000001   1970  ...  Private Citizens & Property    1.0
1  197000000002   1970  ...      Government (Diplomatic)    0.0
2  197001000001   1970  ...          Journalists & Media    1.0
3  197001000002   1970  ...      Government (Diplomatic)    NaN
4  197001000003   1970  ...      Government (Diplomatic)    NaN

[5 rows x 16 columns]

#Quantidade de casos, por país e por ano

In [39]:
df_ac = df.groupby(['iyear', 'country_txt']).agg({'eventid': 'count', 
                                                  'region_txt': 'first',
                                                  'latitude':'first',
                                                  'longitude':'first'})
df_ac.reset_index(['iyear','country_txt'], inplace=True)

df_ac.rename(columns={'eventid':'total_attacks', 
                              'iyear':'year', 
                              'region_txt':'region'}, inplace=True)

#df_with_codes.sort_values(by='year', inplace=True)

In [40]:
fig = px.scatter_geo(df_ac, lat="latitude", lon="longitude", color="region", 
                     hover_name="country_txt", size="total_attacks",
                     animation_frame="year",
                     projection="natural earth",
                     #template="plotly_dark",
                     template="seaborn"
                     )


fig.show()

#Quantidade de casos total em cada país


In [41]:
df_grouped = df.groupby('country_txt').agg({'eventid': 'count', 
                                            'region_txt': 'first',
                                            'latitude':'first',
                                            'longitude':'first'})

df_grouped.reset_index(inplace=True)

df_grouped.rename(columns={'eventid':'total_attacks', 
                       'region_txt':'region'}, inplace=True)

fig = px.scatter_geo(df_grouped, lat="latitude", lon="longitude", color="region", 
                     hover_name="country_txt", size="total_attacks",
                     projection="orthographic")
fig.show()

#Tipos e quantidades de ataques, por região

In [42]:
#df attack region
df_ar = df.groupby(['region_txt', 'attacktype']).agg({'eventid': 'count'})
df_ar.reset_index(['region_txt','attacktype'], inplace=True)

df_ar.rename(columns={'eventid':'total_attacks', 
                            'region_txt':'region'}, inplace=True)
df_ar

region                           attacktype  total_attacks
0    Australasia & Oceania                        Armed Assault             51
1    Australasia & Oceania                        Assassination             36
2    Australasia & Oceania                    Bombing/Explosion             75
3    Australasia & Oceania       Facility/Infrastructure Attack             71
4    Australasia & Oceania                            Hijacking              3
..                     ...                                  ...            ...
103         Western Europe                            Hijacking             67
104         Western Europe  Hostage Taking (Barricade Incident)             89
105         Western Europe          Hostage Taking (Kidnapping)            269
106         Western Europe                      Unarmed Assault            148
107         Western Europe                              Unknown            265

[108 rows x 3 columns]

In [43]:
fig = px.bar(df_ar,
             x='region',
             y='total_attacks',
             color='attacktype')

fig.show()

#Distribuição dos ataques ao longo do tempo, por região

In [44]:
fig = px.violin(df, y='iyear', box=True, color='region_txt')

fig.show()

# Distribuição dos tipos de ataques ao longo do tempo

In [45]:
fig = px.scatter(df,
                 y='region_txt',
                 x='iyear',
                 color='attacktype',
                 marginal_x='histogram')

fig.show()

#Dash


In [65]:
%%writefile my_dash_app.py
import dash
import dash_core_components as dcc
import dash_html_components as html
import plotly.express as px
import pandas as pd


external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = dash.Dash(__name__, external_stylesheets=external_stylesheets)

data = pd.read_csv('/content/archive.zip', compression='zip', encoding='ISO-8859-1')
df = data[['eventid', 'iyear', 'imonth', 'iday', 'country', 'country_txt', 'region',
          'region_txt', 'city', 'latitude', 'longitude', 'multiple', 'success', 
          'attacktype1_txt', 'targtype1_txt', 'nkill']].copy()
df.rename(columns = {"attacktype1_txt": "attacktype"}, inplace=True)


#Dataframe para plotar o PRIMEIRO gráfico
df_ac = df.groupby(['iyear', 'country_txt']).agg({'eventid': 'count', 
                                                  'region_txt': 'first',
                                                  'latitude':'first',
                                                  'longitude':'first'})
df_ac.reset_index(['iyear','country_txt'], inplace=True)
df_ac.rename(columns={'eventid':'total_attacks', 
                              'iyear':'year', 
                              'region_txt':'region'}, inplace=True)


#Dataframe para plotar o SEGUNDO gráfico
df_grouped = df.groupby('country_txt').agg({'eventid': 'count', 
                                            'region_txt': 'first',
                                            'latitude':'first',
                                            'longitude':'first'})
df_grouped.reset_index(inplace=True)
df_grouped.rename(columns={'eventid':'total_attacks', 
                       'region_txt':'region'}, inplace=True)

#Dataframe para plotar o TERCEIRO gráfico
df_ar = df.groupby(['region_txt', 'attacktype']).agg({'eventid': 'count'})
df_ar.reset_index(['region_txt','attacktype'], inplace=True)

df_ar.rename(columns={'eventid':'total_attacks', 
                            'region_txt':'region'}, inplace=True)



#GRÁFICOS
fig_map1 = px.scatter_geo(df_ac, lat="latitude", lon="longitude", color="region", 
                     hover_name="country_txt", size="total_attacks",
                     animation_frame="year",
                     projection="natural earth",
                     template="seaborn"
                     )

fig_map2 = px.scatter_geo(df_grouped, lat="latitude", lon="longitude", color="region", 
                     hover_name="country_txt", size="total_attacks",
                     projection="orthographic")

fig_attacks1 = px.bar(df_ar,
             x='region',
             y='total_attacks',
             color='attacktype')

fig_attacks2 = px.violin(df, y='iyear', box=True, color='region_txt')

fig_attacks3 = px.scatter(df,
                 y='region_txt',
                 x='iyear',
                 color='attacktype',
                 marginal_x='histogram')


app.layout = html.Div(children=[
    # All elements from the top of the page
    html.Div([
        html.H1(children='Terrorismo Global - Análise'),

        html.H3(children='''
            Quantidade de ataques terroristas, em esfera global, ao longo dos anos.
        '''),

        dcc.Graph(
            id='graph1',
            figure=fig_map1
        ),  
    ]),
    # New Div for all elements in the new 'row' of the page
    html.Div([

        html.H3(children='''
            Quantidade total de ataques terroristas nos países em que esses ocorreram.
        '''),

        dcc.Graph(
            id='graph2',
            figure=fig_map2
        ),  
    ]),
    
    html.Div([

        html.H3(children='''
            Quantidade total de ataques e de cada um dos seus tipos, por região.
        '''),

        dcc.Graph(
            id='graph3',
            figure=fig_attacks1
        ),  
    ]),

    html.Div([

        html.H3(children='''
            Distribuição dos ataques ao longo dos anos, por cada região. 
        '''),

        dcc.Graph(
            id='graph4',
            figure=fig_attacks2
        ),  
    ]),
  
    html.Div([

        html.H3(children='''
          Distribuição dos tipos de ataques aos longo do tempo.
        '''),

        dcc.Graph(
            id='graph5',
            figure=fig_attacks3
        ),  
    ]),
])

if __name__ == '__main__':
    app.run_server(debug=True, use_reloader=False)

Overwriting my_dash_app.py


In [55]:
download_ngrok()

In [66]:
retorno = get_tunnel()
print(retorno)
!python my_dash_app.py

Response(url='https://37bfda903cf9.ngrok.io', error=None)
sys:1: DtypeWarning:

Columns (4,6,31,33,61,62,63,76,79,90,92,94,96,114,115,121) have mixed types.Specify dtype option on import or set low_memory=False.

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app "my_dash_app" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: on
